In [1]:
! pip install --quiet requests

In [10]:
import requests
import os
import json
from typing import Any

In [20]:
class TTRSS:
    def __init__(self, url: str) -> None:
        self.url = url
        self.sid = None

    def _make_request(self, op: str, **kwargs: Any) -> Any:
        data = {"op": op, **kwargs}
        if self.sid is not None:
            data["sid"] = self.sid

        r = requests.post(self.url, json=data)
        r.raise_for_status()
        return r.json()

    def login(self, user: str, password: str) -> None:
        body = self._make_request("login", user=user, password=password)
        if "session_id" in body["content"]:
            self.sid = body["content"]["session_id"]
        else:
            raise Exception(f"Login to TTRSS failed with error {body}")

    def _assert_logged_in(self) -> None:
        if self.sid is None:
            raise Exception("Must be logged in to use this method")

    def get_feeds(self, cat_id: int = -3) -> list[dict]:
        self._assert_logged_in()
        return self._make_request("getFeeds", cat_id=cat_id)

    def subscribe(self, feed_url: str, cat_id: int = 0) -> None:
        self._assert_logged_in()
        body = self._make_request(
            "subscribeToFeed", feed_url=feed_url, category_id=cat_id
        )
        if body["status"]["code"] != 1:
            raise Exception(f"Failed to subscribe to {feed_url}: {r.json()['status']}")

In [21]:
url = os.environ["TTRSS_URL"]
user = os.environ["TTRSS_USER"]
password = os.environ["TTRSS_PASS"]

In [22]:
ttrss = TTRSS(url)

In [23]:
ttrss.login(user, password)

In [24]:
ttrss.get_feeds(11)

{'seq': 0,
 'status': 0,
 'content': [{'feed_url': 'https://nas.franpenedo.com/rss-bridge/?action=display&bridge=AO3Bridge&context=Work&id=45519316&format=atom',
   'title': 'Back, Black, and Ready to Snack',
   'id': 214,
   'unread': 0,
   'has_icon': True,
   'cat_id': 11,
   'last_updated': 1698266675,
   'order_id': 0},
  {'feed_url': 'https://nas.franpenedo.com/rss-bridge/?action=display&bridge=AO3Bridge&context=Work&id=45526351&format=atom',
   'title': 'Harry Potter and the Tri-Wizard Tournament.',
   'id': 213,
   'unread': 4,
   'has_icon': True,
   'cat_id': 11,
   'last_updated': 1698265341,
   'order_id': 0},
  {'feed_url': 'https://nas.franpenedo.com/rss-bridge/?action=display&bridge=AO3Bridge&context=Work&id=50482837&format=atom',
   'title': 'The Space left behind',
   'id': 209,
   'unread': 0,
   'has_icon': True,
   'cat_id': 11,
   'last_updated': 1698265586,
   'order_id': 0},
  {'feed_url': 'https://nas.franpenedo.com/rss-bridge/?action=display&bridge=AO3Bridge&co